In [1]:
import cobra
import matplotlib.pyplot as plt
import multiprocessing as mp
import numpy as np
import pandas as pd
import scipy.stats

from time import time
from operator import itemgetter


In [4]:
Recon3D = cobra.io.load_matlab_model('Recon3D.mat')

In [7]:
start_time = time()

# modifiable variables: cell # (max 8444), gene # (max 1800), threshold is % unique cells
cells = 8444
genes = 1800
threshold = .7
threads = 8
plot = False

# import model and make objective atp_c
# ALCD2X, etoh_c 

# rxnName = 'atp_drain'
# met_name = 'atp_c'
# stoich = [-1]
# tempRxn = cobra.Reaction(rxnName)
# tempDrainMetDict = {Recon3D.metabolites.get_by_id(met_name): s for name, s in zip(met_name, stoich)}
# tempRxn.add_metabolites(tempDrainMetDict)
# live.add_reaction(tempRxn)
# Recon3D.objective = rxnName

Recon3D.reactions.get_by_id("ETOHt").lower_bound = 1000
Recon3D.reactions.get_by_id("ETOHt").upper_bound = 1000
Recon3D.objective = "ALCD2x"

def optimize_for_gene(name, expression):
    # return flux balance analysis result for a particular gene and cell #
    print("Model Start")
    global modelOriginal
    with Recon3D as model:
        # get expression data from the scRNAseq data set
        # expression = data.loc[name][cell_num]
        # retrieve the reaction for the gene
        reactions = model.genes.get_by_id(gene_info[name]).reactions
        # change bounds for all reactions associated with the gene
        for j in reactions:
            j.lower_bound = expression * 100
            j.upper_bound = expression * 100
        fbas = model.optimize('maximize')
        # return gene name, cell #, and objective value so that we can recover
        # results from multiprocessing
        return [name, fbas.objective_value]


# read in scRNAseq data set
data = pd.read_csv('GSE115469_Data.csv', index_col=0)
# gene names should be the 0th column, which is the index column
genes_in_sc = data.index
# read in the map from gene name -> model name
f = open('map.txt', 'r')
dict_temp = f.readlines()
list_dict = dict_temp[0].split(';')
gene_info = {}
for i in list_dict:
    if i == '':
        continue
    tempkey = i.split(',')[0]
    tempval = i.split(',')[1]
    gene_info[tempkey] = tempval
f.close()
# find all genes that exist in the scRNAseq set and in the model
gene_matches = [genes_in_sc[i] for i in range(len(genes_in_sc)) if genes_in_sc[i] in gene_info.keys()]
# prepare a list to receive the ApplyResult objects from multiprocessing
results = []
# prepare a list to make plotting axes easier
dimnames = []
print('starting models')
# generate 50 random numbers to select 50 random cells to observe
# cell_nums = random.sample(range(len(list(data.loc[gene_matches[0]]))), 750)
# gene_nums = random.sample(range(len(gene_matches)), 10)
# multiprocessing w/ 3 threads
p = mp.Pool(threads)
# do FBA on the first 10 genes to make it faster for now
for num in range(len(gene_matches)):
    print('starting async')
    # find unique expression levels
    unique_expression_levels, ucind = np.unique(data.loc[gene_matches[num]][:cells], return_inverse = True)
    if len(unique_expression_levels) < threshold * cells:
        print('Skipping Gene %i' % (num))
        continue
#     for i in ucind:
#         print("Gene #: %d Cell #: %d" % (num, i))
#         print("Starting Async")
#     for i in range(len(unique_expression_levels)):
#         print("Gene #: %d Cell #: %d" % (num, ucind[i]))
#         print("Starting Async")
#         result = p.apply_async(optimize_for_gene, args = (gene_matches[num], unique_expression_levels[i]))
#         results.append([result, num, ucind[i]])
    for i in range(len(unique_expression_levels)):
        # helps to check which threads are running atm
        print("gene #: %d cell #: %d" % (num, i))
        print('starting async')
        # find the place where the unique expression levels are 
        cell_locs = [index for index in range(len(ucind)) if ucind[index] == i]
        # put the ApplyResult object in a list
        temp_result = p.apply_async(optimize_for_gene, args=(gene_matches[num], i))
        # record instances of unique expression level results
        for ind in cell_locs:
            results.append([temp_result, num, ind])
# we're not using these threads anymore so we can move on
p.close()
# wait for all the threads to finish before we start converting results to
# a usable form
p.join()
# fetch the results of the ApplyResult object for the entire list
# make the ApplyResults into aa pandas dataframe to make it easier to sort
results_pd = pd.DataFrame.from_records(results)
# sort by gene # and cell # within gene #
results_pd = results_pd.sort_values([1, 2])
results_pd = results_pd.reset_index()
# get the result
results_fetched = [[results_pd.loc[i][0].get(), results_pd.loc[i][1], results_pd.loc[i][2]]
                   for i in range(results_pd.shape[0])]
# make it a pandas data frame so its easier to transform
df = pd.DataFrame.from_records(results_fetched)
# sort by the gene name first, then by the cell number within the gene name
df.sort_values(by=[1, 2])
# pivot converts a 1x10,0000 list to a 10x1,000 array with rownames that match
# unique values of column 0, and column names that match unique values of column 1
# and values that match column 2
df = df.pivot(index=1, columns=2, values=0)
# the dimnames should match the unique values of column 0 (gene names)
for i in range(int(results_pd.shape[0]/cells)):
    dimnames.append(df.iloc[i][0][0])
# convert the results back into a numpy array so that plotting is easer.
results_T = np.array(df.applymap(lambda x: x[1]))
filename = met_name + 'results' + str(threshold) + 'threshold' + str(cells) + 'cells' + '.txt.gz'
dimfilename = met_name + 'dimensions_of_results' + str(threshold) + 'threshold' + str(cells) + 'cells' + '.txt'
np.savetxt(filename, results_T)
dimf = open(dimfilename, 'w')
for i in dimnames:
    dimf.write(i + ';')
dimf.close()
print(time()-start_time)
if plot:
    print('plotting')
    # subtract the mode to deal with FBA values that are uninteresting
    for i in range(len(results_T)):
        results_T[i] -= np.ones(len(results_T[i])) * scipy.stats.mode(results_T[i])[0]
    # set up 100 plots to plot pairwise gene results
    fig, axs = plt.subplots(len(gene_matches[:genes]), len(gene_matches[:genes]))
    # plot all the results
    for i in range(len(results_T[:genes])):
        for j in range(len(results_T[:genes])):
            # print(results_T[i])
            axs[i, j].scatter(results_T[i], results_T[j])
            axs[i, j].set_xlabel(dimnames[j])
            axs[i, j].set_ylabel(dimnames[i])
    plt.show()


starting models
starting async
Skipping Gene 0
starting async
Skipping Gene 1
starting async
Skipping Gene 2
starting async
Skipping Gene 3
starting async
Skipping Gene 4
starting async
Skipping Gene 5
starting async
Skipping Gene 6
starting async
Skipping Gene 7
starting async
Skipping Gene 8
starting async
Skipping Gene 9
starting async
Skipping Gene 10
starting async
Skipping Gene 11
starting async
Skipping Gene 12
starting async
Skipping Gene 13
starting async
Skipping Gene 14
starting async
Skipping Gene 15
starting async
Skipping Gene 16
starting async
Skipping Gene 17
starting async
Skipping Gene 18
starting async
Skipping Gene 19
starting async
Skipping Gene 20
starting async
Skipping Gene 21
starting async
Skipping Gene 22
starting async
Skipping Gene 23
starting async
Skipping Gene 24
starting async
Skipping Gene 25
starting async
Skipping Gene 26
starting async
Skipping Gene 27
starting async
Skipping Gene 28
starting async
Skipping Gene 29
starting async
Skipping Gene 30
st

Starting Async
Gene #: 301 Cell #: 860
Starting Async
Gene #: 301 Cell #: 244
Starting Async
Gene #: 301 Cell #: 5720
Starting Async
Gene #: 301 Cell #: 1739
Starting Async
Gene #: 301 Cell #: 852
Starting Async
Gene #: 301 Cell #: 753
Starting Async
Gene #: 301 Cell #: 6189
Starting Async
Gene #: 301 Cell #: 1136
Starting Async
Gene #: 301 Cell #: 137
Starting Async
Gene #: 301 Cell #: 71
Starting Async
Gene #: 301 Cell #: 837
Starting Async
Gene #: 301 Cell #: 5291
Starting Async
Gene #: 301 Cell #: 5503
Starting Async
Gene #: 301 Cell #: 4160
Starting Async
Gene #: 301 Cell #: 3929
Starting Async
Gene #: 301 Cell #: 2941
Starting Async
Gene #: 301 Cell #: 1465
Starting Async
Gene #: 301 Cell #: 223
Starting Async
Gene #: 301 Cell #: 2675
Starting Async
Gene #: 301 Cell #: 937
Starting Async
Gene #: 301 Cell #: 6778
Starting Async
Gene #: 301 Cell #: 2765
Starting Async
Gene #: 301 Cell #: 5063
Starting Async
Gene #: 301 Cell #: 3436
Starting Async
Gene #: 301 Cell #: 1491
Starting A

Starting Async
Gene #: 301 Cell #: 8042
Starting Async
Gene #: 301 Cell #: 4689
Starting Async
Gene #: 301 Cell #: 5325
Starting Async
Gene #: 301 Cell #: 3818
Starting Async
Gene #: 301 Cell #: 4108
Starting Async
Gene #: 301 Cell #: 3849
Starting Async
Gene #: 301 Cell #: 4377
Starting Async
Gene #: 301 Cell #: 1832
Starting Async
Gene #: 301 Cell #: 3450
Starting Async
Gene #: 301 Cell #: 598
Starting Async
Gene #: 301 Cell #: 3801
Starting Async
Gene #: 301 Cell #: 161
Starting Async
Gene #: 301 Cell #: 4033
Starting Async
Gene #: 301 Cell #: 8338
Starting Async
Gene #: 301 Cell #: 876
Starting Async
Gene #: 301 Cell #: 703
Starting Async
Gene #: 301 Cell #: 6871
Starting Async
Gene #: 301 Cell #: 7289
Starting Async
Gene #: 301 Cell #: 1974
Starting Async
Gene #: 301 Cell #: 1652
Starting Async
Gene #: 301 Cell #: 80
Starting Async
Gene #: 301 Cell #: 453
Starting Async
Gene #: 301 Cell #: 4239
Starting Async
Gene #: 301 Cell #: 2877
Starting Async
Gene #: 301 Cell #: 594
Starting

Gene #: 301 Cell #: 189
Starting Async
Gene #: 301 Cell #: 1362
Starting Async
Gene #: 301 Cell #: 6792
Starting Async
Gene #: 301 Cell #: 7402
Starting Async
Gene #: 301 Cell #: 5330
Starting Async
Gene #: 301 Cell #: 4107
Starting Async
Gene #: 301 Cell #: 3460
Starting Async
Gene #: 301 Cell #: 4590
Starting Async
Gene #: 301 Cell #: 4411
Starting Async
Gene #: 301 Cell #: 3758
Starting Async
Gene #: 301 Cell #: 1138
Starting Async
Gene #: 301 Cell #: 6200
Starting Async
Gene #: 301 Cell #: 6685
Starting Async
Gene #: 301 Cell #: 4705
Starting Async
Gene #: 301 Cell #: 7995
Starting Async
Gene #: 301 Cell #: 2916
Starting Async
Gene #: 301 Cell #: 2794
Starting Async
Gene #: 301 Cell #: 1271
Starting Async
Gene #: 301 Cell #: 4456
Starting Async
Gene #: 301 Cell #: 61
Starting Async
Gene #: 301 Cell #: 83
Starting Async
Gene #: 301 Cell #: 7251
Starting Async
Gene #: 301 Cell #: 6015
Starting Async
Gene #: 301 Cell #: 5320
Starting Async
Gene #: 301 Cell #: 3619
Starting Async
Gene 

Gene #: 301 Cell #: 5536
Starting Async
Gene #: 301 Cell #: 3676
Starting Async
Gene #: 301 Cell #: 173
Starting Async
Gene #: 301 Cell #: 1236
Starting Async
Gene #: 301 Cell #: 7936
Starting Async
Gene #: 301 Cell #: 37
Starting Async
Gene #: 301 Cell #: 793
Starting Async
Gene #: 301 Cell #: 128
Starting Async
Gene #: 301 Cell #: 2826
Starting Async
Gene #: 301 Cell #: 3246
Starting Async
Gene #: 301 Cell #: 4364
Starting Async
Gene #: 301 Cell #: 4904
Starting Async
Gene #: 301 Cell #: 1409
Starting Async
Gene #: 301 Cell #: 6987
Starting Async
Gene #: 301 Cell #: 2302
Starting Async
Gene #: 301 Cell #: 642
Starting Async
Gene #: 301 Cell #: 5459
Starting Async
Gene #: 301 Cell #: 7914
Starting Async
Gene #: 301 Cell #: 3543
Starting Async
Gene #: 301 Cell #: 5227
Starting Async
Gene #: 301 Cell #: 4222
Starting Async
Gene #: 301 Cell #: 3231
Starting Async
Gene #: 301 Cell #: 4020
Starting Async
Gene #: 301 Cell #: 6935
Starting Async
Gene #: 301 Cell #: 7239
Starting Async
Gene #

...

Gene #: 913 Cell #: 8158
Starting Async
Gene #: 913 Cell #: 219
Starting Async
Gene #: 913 Cell #: 2013
Starting Async
Gene #: 913 Cell #: 6296
Starting Async
Gene #: 913 Cell #: 5957
Starting Async
Gene #: 913 Cell #: 6131
Starting Async
Gene #: 913 Cell #: 262
Starting Async
Gene #: 913 Cell #: 2028
Starting Async
Gene #: 913 Cell #: 6048
Starting Async
Gene #: 913 Cell #: 8054
Starting Async
Gene #: 913 Cell #: 4097
Starting Async
Gene #: 913 Cell #: 6153
Starting Async
Gene #: 913 Cell #: 1896
Starting Async
Gene #: 913 Cell #: 1876
Starting Async
Gene #: 913 Cell #: 6072
Starting Async
Gene #: 913 Cell #: 2170
Starting Async
Gene #: 913 Cell #: 1403
Starting Async
Gene #: 913 Cell #: 8072
Starting Async
Gene #: 913 Cell #: 139
Starting Async
Gene #: 913 Cell #: 6721
Starting Async
Gene #: 913 Cell #: 245
Starting Async
Gene #: 913 Cell #: 7440
Starting Async
Gene #: 913 Cell #: 1872
Starting Async
Gene #: 913 Cell #: 5136
Starting Async
Gene #: 913 Cell #: 6711
Starting Async
Gene

Gene #: 913 Cell #: 2412
Starting Async
Gene #: 913 Cell #: 171
Starting Async
Gene #: 913 Cell #: 1165
Starting Async
Gene #: 913 Cell #: 1603
Starting Async
Gene #: 913 Cell #: 597
Starting Async
Gene #: 913 Cell #: 996
Starting Async
Gene #: 913 Cell #: 4281
Starting Async
Gene #: 913 Cell #: 666
Starting Async
Gene #: 913 Cell #: 371
Starting Async
Gene #: 913 Cell #: 4900
Starting Async
Gene #: 913 Cell #: 188
Starting Async
Gene #: 913 Cell #: 893
Starting Async
Gene #: 913 Cell #: 4213
Starting Async
Gene #: 913 Cell #: 1584
Starting Async
Gene #: 913 Cell #: 1729
Starting Async
Gene #: 913 Cell #: 7753
Starting Async
Gene #: 913 Cell #: 5751
Starting Async
Gene #: 913 Cell #: 8018
Starting Async
Gene #: 913 Cell #: 8350
Starting Async
Gene #: 913 Cell #: 7638
Starting Async
Gene #: 913 Cell #: 6762
Starting Async
Gene #: 913 Cell #: 7261
Starting Async
Gene #: 913 Cell #: 85
Starting Async
Gene #: 913 Cell #: 5649
Starting Async
Gene #: 913 Cell #: 1904
Starting Async
Gene #: 9

Starting Async
Gene #: 913 Cell #: 6755
Starting Async
Gene #: 913 Cell #: 6253
Starting Async
Gene #: 913 Cell #: 6181
Starting Async
Gene #: 913 Cell #: 3163
Starting Async
Gene #: 913 Cell #: 5105
Starting Async
Gene #: 913 Cell #: 6676
Starting Async
Gene #: 913 Cell #: 23
Starting Async
Gene #: 913 Cell #: 2903
Starting Async
Gene #: 913 Cell #: 1740
Starting Async
Gene #: 913 Cell #: 950
Starting Async
Gene #: 913 Cell #: 6201
Starting Async
Gene #: 913 Cell #: 66
Starting Async
Gene #: 913 Cell #: 436
Starting Async
Gene #: 913 Cell #: 7698
Starting Async
Gene #: 913 Cell #: 7755
Starting Async
Gene #: 913 Cell #: 2082
Starting Async
Gene #: 913 Cell #: 5566
Starting Async
Gene #: 913 Cell #: 3016
Starting Async
Gene #: 913 Cell #: 6699
Starting Async
Gene #: 913 Cell #: 399
Starting Async
Gene #: 913 Cell #: 5478
Starting Async
Gene #: 913 Cell #: 6744
Starting Async
Gene #: 913 Cell #: 277
Starting Async
Gene #: 913 Cell #: 2195
Starting Async
Gene #: 913 Cell #: 3424
Starting

Starting Async
Gene #: 913 Cell #: 135
Starting Async
Gene #: 913 Cell #: 2470
Starting Async
Gene #: 913 Cell #: 7550
Starting Async
Gene #: 913 Cell #: 1339
Starting Async
Gene #: 913 Cell #: 4203
Starting Async
Gene #: 913 Cell #: 2256
Starting Async
Gene #: 913 Cell #: 8397
Starting Async
Gene #: 913 Cell #: 4044
Starting Async
Gene #: 913 Cell #: 4521
Starting Async
Gene #: 913 Cell #: 4104
Starting Async
Gene #: 913 Cell #: 5157
Starting Async
Gene #: 913 Cell #: 4944
Starting Async
Gene #: 913 Cell #: 7057
Starting Async
Gene #: 913 Cell #: 8211
Starting Async
Gene #: 913 Cell #: 4501
Starting Async
Gene #: 913 Cell #: 1928
Starting Async
Gene #: 913 Cell #: 1530
Starting Async
Gene #: 913 Cell #: 7883
Starting Async
Gene #: 913 Cell #: 5380
Starting Async
Gene #: 913 Cell #: 8341
Starting Async
Gene #: 913 Cell #: 5414
Starting Async
Gene #: 913 Cell #: 5355
Starting Async
Gene #: 913 Cell #: 7221
Starting Async
Gene #: 913 Cell #: 1376
Starting Async
Gene #: 913 Cell #: 1952
S

KeyboardInterrupt: 